<font color=red>**Danger zone:**</font> you'll be fine-tuning a model to generate positive, negative or even toxic reviews. We'll be doing this for fun, but this is also the technique for [review bombing](https://en.wikipedia.org/wiki/Review_bomb), bot farms on social media and other less than dignified stuff. It is ultimately your decision how you apply this knowledge, but before you choose, ask yourself: is this why you chose to learn ML?


# LLMs Alignment with Reinforcement Learning from human feedback (RLHF).

_based on the [original notebook](https://github.com/antndlcrx/oxford-llms-workshop/blob/main/materials/seminars/day_3/8_LLMs%20alignment%20with%20RLHF.ipynb) by Ilya Boytsov for the Oxford LLMs workshop_



In this session, you're gonna fine-tune a language model with reinforcement learning to make it generate good (or bad) reviews.

To perform RL-based fine-tuning, we'll use a new (in this course) library called [Transformer Reinforcement Learning (TRL)](https://huggingface.co/docs/trl). TRL implements the main reinforcement learning components of RLHF: reward modeling and fine-tuning with PPO.

![img](https://huggingface.co/datasets/trl-internal-testing/example-images/resolve/main/images/TRL-readme.png)

In [2]:
%pip install -q trl==0.7.4 transformers==4.33.1 accelerate==0.28.0 datasets peft==0.5.0

  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.

[notice] A new release of pip is available: 23.0.1 -> 24.3.1
[notice] To update, run: python3 -m pip install --upgrade pip


### Tutorial: align the model to generate positive movie reviews

To see how TRL works, we'll use it to align GPT2 on IMDB dataset to generate positive (or negative) movie reviews. In fact, __it's your choice whether you want positive or negative reviews.__

But before you choose, let's take a look at the baseline model: a GPT-2 fine-tuned on generating arbitrary movie reviews.

In [1]:
from tqdm.auto import tqdm, trange

In [2]:
import torch
import transformers
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
main_tokenizer = transformers.AutoTokenizer.from_pretrained("lvwerra/gpt2-imdb")
main_model = transformers.AutoModelForCausalLM.from_pretrained("lvwerra/gpt2-imdb", device_map=device)

/home/jupyter/.local/lib/python3.10/site-packages/huggingface_hub/file_download.py:795: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
2024-12-25 06:23:01.623830: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
/home/jupyter/.local/lib/python3.10/site-packages/huggingface_hub/file_download.py:795: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


In [3]:
inputs = main_tokenizer("The movie", return_tensors='pt').to(device)
generated_ids = main_model.generate(**inputs, max_new_tokens=50, do_sample=True)
print("\nGenerated text:", main_tokenizer.decode(generated_ids.flatten().cpu().numpy().tolist()))

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.



Generated text: The movie I loved it was definitely the movie that would convince me to rent "A Day in the Life". It reminded me of the old old Hitchcock movies like "Shakespeare In Love" and "Citizen Kane". My guess is there are many more who


If you run this cell a couple of times, you'll see that the model generates both positive, negative and neutral reviews in some proportion. What we're gonna do next is teach the model to generate more positive (or negative) reviews.

Similarly to InstructGPT, we're gonna do that in 2 stages:
- **train a reward model** to assign higher values to positive (or negative) reviews
- fine-tune the language model to **maximize that reward using [proximal policy optimization](https://openai.com/research/openai-baselines-ppo)**



## Stage 1: train a reward model

First, we'll train a BERT-like model as our reward model. We'll generate a synthetic pairwise rankings to emulate human rankings.

__Q:__ why do I need a reward model? Can I just use a pre-trained sentiment classifier? <br> __A:__ Yes, you can - but that only works for movie reviews. But this tutorial will teach you how to do RLHF for any kind objective.


__If you actually want to maximize sentiment (or other "label") instead of human preferences, train reward model as a classifier! (see week5)__


In [4]:
# We'll be fine-tuning a small BERT-like model for now. Please try other models for the main assignment.
reward_model = transformers.AutoModelForSequenceClassification.from_pretrained("distilbert-base-cased", device_map=device)
reward_tokenizer = transformers.AutoTokenizer.from_pretrained("distilbert-base-cased")

Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-cased and are newly initialized: ['classifier.weight', 'pre_classifier.weight', 'pre_classifier.bias', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


__Note that__ the reward model has a separate tokenizer, different from the main model. They don't need to be the same for RLHF fine-tuning.

In [5]:
# To train a reward model, you need a dataset (or generator) of positive-negative pairs.
# Each training sample should be a dict with 4 keys:
#  - input_ids_chosen, attention_mask_chosen = tokenizer("A sentence that human labeler likes more")
#  - input_ids_rejected, attention_mask_rejected = tokenizer("A sentence that human labeler likes less")

import torch
import datasets

class IMDBPairwiseDataset(torch.utils.data.Dataset):
    """ A dataset of all possible pairs of chosen and texts in TRT reward training format """

    column_names = ['input_ids_chosen', 'attention_mask_chosen', 'input_ids_rejected', 'attention_mask_rejected']

    def __init__(self, imdb, tokenizer, accepted_label: int):
        super().__init__()
        self.tokenizer = tokenizer
        self.chosen_texts = [row['text'] for row in imdb if row['label'] == accepted_label]
        self.rejected_texts = [row['text'] for row in imdb if row['label'] != accepted_label]
        assert self.chosen_texts, f"no texts with label {accepted_label}"
        print(f"Found {len(self.chosen_texts)} chosen and {len(self.rejected_texts)} rejected texts, {len(self)} pairs")

    def __len__(self):
        return len(self.chosen_texts) * len(self.rejected_texts)  # all pairs

    def __getitem__(self, index: int):
        chosen = self.tokenizer(self.chosen_texts[index // len(self.chosen_texts)], truncation=True)
        rejected = self.tokenizer(self.rejected_texts[index % len(self.chosen_texts)], truncation=True)
        return dict(input_ids_chosen=chosen['input_ids'], attention_mask_chosen=chosen['attention_mask'],
                    input_ids_rejected=rejected['input_ids'], attention_mask_rejected=rejected['attention_mask'])

In [6]:
TARGET_LABEL = 0   # and make sure it works by reviewing the sample printed below
imdb = datasets.load_dataset("imdb", split='train')
reward_data = IMDBPairwiseDataset(imdb, reward_tokenizer, accepted_label=TARGET_LABEL)

sample = reward_data[31337]
print('CHOSEN:', reward_tokenizer.decode(sample['input_ids_chosen']))
print('REJECTED:', reward_tokenizer.decode(sample['input_ids_rejected']))

Found 12500 chosen and 12500 rejected texts, 156250000 pairs
CHOSEN: [CLS] If only to avoid making this type of film in the future. This film is interesting as an experiment but tells no cogent story. < br / > < br / > One might feel virtuous for sitting thru it because it touches on so many IMPORTANT issues but it does so without any discernable motive. The viewer comes away with no new perspectives ( unless one comes up with one while one's mind wanders, as it will invariably do during this pointless film ). < br / > < br / > One might better spend one's time staring out a window at a tree growing. < br / > < br / > [SEP]
REJECTED: [CLS] This movie has some things that are pretty amazing. First, it is supposed to be based on a true story. That, in itself, is amazing that multiple tornadoes would hit the same town at night in the fall - in Nebraska. I wonder if the real town's name was close to " Blainsworth " ( which is the town's name in the movie ). There is an Ainsworth, Nebraska,

We'll be using `trl.RewardTrainer` - a special case of `transformers.Trainer` that you used in the past. `RewardTrainer` accepts the same format of training arguments (e.g. batch size, gradient checkpointing) as before, except that it trains the model for the pairwise reward objective from [the InstructGPT paper](https://arxiv.org/pdf/2203.02155.pdf):

![img](https://i.imgur.com/2JzNAPs.png)

Note that the model itself does not score pairs: it processes chosen ($y_w$) and rejected ($y_l$) samples independently. To minimize this loss, the reward model needs to score chosen sample higher than the rejected one. Note that the formula also assumes some context $x$, which is useful for seq2seq tasks. In our case of movie reviews, $x$ is empty.

In [7]:
import trl

training_args = trl.RewardConfig(  # like transformers.TrainingArguments
    output_dir="reward_model",
    per_device_train_batch_size=32,
    gradient_accumulation_steps=1,
    learning_rate=1.41e-5,
    max_steps=1_000,              # note: training may need more than 1k steps
    logging_steps=50,
    gradient_checkpointing=True,  # reduce memory usage but train ~30% slower
    gradient_checkpointing_kwargs={"use_reentrant": False},
    fp16=True                     # disable this on CPU or on very old GPUs
    # you may add any other hyperparameters that you found useful in weeks 5-7
)

trainer = trl.RewardTrainer(
    model=reward_model,
    args=training_args,
    tokenizer=reward_tokenizer,
    train_dataset=reward_data,
    peft_config=None,  # optionally, you may tune with LoRA, prompt-tuning, etc
)

trainer.train()

[2024-12-22 02:32:54,323] [INFO] [real_accelerator.py:219:get_accelerator] Setting ds_accelerator to cuda (auto detect)


/usr/bin/ld: cannot find -laio: No such file or directory
collect2: error: ld returned 1 exit status
/usr/bin/ld: cannot find -laio: No such file or directory
collect2: error: ld returned 1 exit status
/home/jupyter/.local/lib/python3.10/site-packages/trl/trainer/ppo_config.py:141: UserWarning: The `optimize_cuda_cache` arguement will be deprecated soon, please use `optimize_device_cache` instead.
  warnings.warn(
/home/jupyter/.local/lib/python3.10/site-packages/trl/trainer/reward_trainer.py:174: UserWarning: When using RewardDataCollatorWithPadding, you should set `max_length` in RewardConfig. It will be set to `512` by default, but you should do it yourself in the future.
  warnings.warn(
/home/jupyter/.local/lib/python3.10/site-packages/trl/trainer/reward_trainer.py:191: UserWarning: When using RewardDataCollatorWithPadding, you should set `remove_unused_columns=False` in your RewardConfig we have set it for you, but you should do it yourself in the future.
  warnings.warn(
/home/j

{'loss': 0.5346, 'learning_rate': 1.34091e-05, 'epoch': 0.0}


/home/jupyter/.local/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:2436: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(
/home/jupyter/.local/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:2436: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(
  5%|▌         | 51/1000 [00:45<08:12,  1.93it/s]/home/jupyter/.local/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:2436: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(
/home/jupyter/.local/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:2436: UserWarning: `max_length` is ignored when `padding`=`True` and there is no tru

{'loss': 0.1763, 'learning_rate': 1.2718200000000001e-05, 'epoch': 0.0}


...

/home/jupyter/.local/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:2436: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(
/home/jupyter/.local/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:2436: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(
 95%|█████████▌| 951/1000 [08:39<00:25,  1.92it/s]/home/jupyter/.local/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:2436: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(
/home/jupyter/.local/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:2436: UserWarning: `max_length` is ignored when `padding`=`True` and there is no tr

{'loss': 0.0731, 'learning_rate': 2.82e-08, 'epoch': 0.0}


100%|██████████| 1000/1000 [09:12<00:00,  1.81it/s]

{'train_runtime': 552.4724, 'train_samples_per_second': 57.921, 'train_steps_per_second': 1.81, 'train_loss': 0.11066102957725525, 'epoch': 0.0}


TrainOutput(global_step=1000, training_loss=0.11066102957725525, metrics={'train_runtime': 552.4724, 'train_samples_per_second': 57.921, 'train_steps_per_second': 1.81, 'train_loss': 0.11066102957725525, 'epoch': 0.0})

In [8]:
reward_model.gradient_checkpointing_disable()
reward_model.eval()

DistilBertForSequenceClassification(
  (distilbert): DistilBertModel(
    (embeddings): Embeddings(
      (word_embeddings): Embedding(28996, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (transformer): Transformer(
      (layer): ModuleList(
        (0-5): 6 x TransformerBlock(
          (attention): MultiHeadSelfAttention(
            (dropout): Dropout(p=0.1, inplace=False)
            (q_lin): Linear(in_features=768, out_features=768, bias=True)
            (k_lin): Linear(in_features=768, out_features=768, bias=True)
            (v_lin): Linear(in_features=768, out_features=768, bias=True)
            (out_lin): Linear(in_features=768, out_features=768, bias=True)
          )
          (sa_layer_norm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
          (ffn): FFN(
            (dropout): Dropout(p=0.1, inplace=False)
 

### Sanity-check the reward model (1 point)

Let's check how our reward model performs.

__Your task__ is to measure how often does your reward model can rank a pair of (chosen and rejected) reviews correctly. Please measure this separately for train data (`imdb`) and a separate test set loaded below.

In [9]:

for sample_index in 45, 16000:
  print('TEXT:', imdb[sample_index]['text'])
  inputs = reward_tokenizer(
      imdb[sample_index]['text'], truncation=True, return_tensors='pt').to(device)
  with torch.no_grad():
    reward = reward_model(**inputs).logits[0, 0].item()
    print("REWARD:", reward)
  print('LABEL:', imdb[sample_index]['label'])
  print()

# note: your reward model may produce different absolute rewards.
# This is fine as long as the rewards are ordered correctly (most of the time)

TEXT: This movie sucked. It really was a waste of my life. The acting was atrocious, the plot completely implausible. Long, long story short, these people get "terrorized" by this pathetic "crazed killer", but completely fail to fight back in any manner. And this is after they take a raft on a camping trip, with no gear, and show up at a campsite that is already assembled and completely stocked with food and clothes and the daughters headphones. Additionally, after their boat goes missing, they panic that they're stuck in the woods, but then the daughters boyfriend just shows up and they apparently never consider that they could just hike out of the woods like he did to get to them. Like I said, this movie sucks. A complete joke. Don't let your girlfriend talk you into watching it.
REWARD: 5.08203125
LABEL: 0

TEXT: Good: Engaging cinematic firefights, great presentation, vehicles are actually fun to drive, fairly appealing multiplayer, faithful to the movie, and the list goes on.<br /

In [11]:
from sklearn.metrics import roc_auc_score

imdb_test = datasets.load_dataset("imdb", split='test')

In [13]:
labels = []
rewards = []
for sample_index in trange(len(imdb_test)):
  inputs = reward_tokenizer(imdb_test[sample_index]['text'], truncation=True, return_tensors='pt').to(device)
  with torch.no_grad():
    reward = reward_model(**inputs).logits[0, 0].item()
    rewards.append(reward)
  labels.append(imdb_test[sample_index]['label'])

print(1 - roc_auc_score(labels, rewards))

100%|██████████| 25000/25000 [04:18<00:00, 96.80it/s] 


0.9717145632


### Reward-guided generation (1 point)

If you did everything right, by now you should have a decent reward model. Before we use it for reinforcement learning, let's see if we can align model samples without any training.

To do so, you can use reward-guided inference: __generate N=16 samples, then select the one with the highest reward__ (according to your reward model).

For this problem, it's on you to demonstrate whether or not your code works. Find at least 5 neutral prompts such as "This movie is" (...), generate samples, rank them based on reward and show which samples get the highest reward.

Note: it is faster to generate samples in parallel, rather than sequentially, as follows:




In [14]:
inputs = main_tokenizer(["It was"] * 5, return_tensors='pt').to(device)
for candidate in main_model.generate(**inputs, max_new_tokens=50, do_sample=True):
  print("Sample:", main_tokenizer.decode(candidate.flatten().cpu().numpy().tolist()))

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Sample: It was almost like I'd never heard of the film before I saw it. I knew of the opening sequence because I remember being told it was part of the early-'60's and I was still getting used to it. When I first saw it, I
Sample: It was an absolute no-brainer that the director would have to be nominated for the Academy Award. Now for the script. What follows is the story (I will not repeat myself here, as it is too long for one movie) of some pretty old-
Sample: It was also very strange it has no title of "Drama". I will be the last to write an example of that in a movie, but the original was never released in any form, other than a trailer released by American distributor HARDMADE.
Sample: It was so strange I really don't understand the way things were going until I sat down for it. And it seems, after watching it on TV, that you've become so accustomed to it, that this little movie is quite unbelievable. It also is a
Sample: It was a truly spectacular movie. All the cast performed w

In [15]:
prompts = ['This movie is']

In [22]:
import numpy as np

def ranked_generations(prompt, N=16):
    inputs = main_tokenizer([prompt] * N, return_tensors='pt').to(device)
    candidates = main_model.generate(**inputs, max_new_tokens=50, do_sample=True)
    samples = np.array([main_tokenizer.decode(candidate.flatten().cpu().numpy().tolist()) for candidate in candidates])

    rewards = []
    for sample in samples:
        inputs = reward_tokenizer(sample, truncation=True, return_tensors='pt').to(device)
        with torch.no_grad():
            reward = reward_model(**inputs).logits[0, 0].item()
            rewards.append(reward)

    rewards = np.array(rewards)
    ranks = np.argsort(-rewards)
    for sample in samples[ranks]:
        print(sample)
        print('===========================================')

In [23]:
ranked_generations('This film is')

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


This film is not that bad, and as mentioned before, it's not all bad movies with bad plot. Instead of a typical "Hollywood" movie where the story is set on a spaceship, the movie is a full movie of a series of scenes involving a
This film is about two American families separated by the fact that a very wealthy family members are going to be losing their home at the funeral and they are coming home early and being treated by local police. They have nothing like the typical elderly or mentally handicapped living on
This film is so good you might want to throw in a few more.<|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endo

In [24]:
ranked_generations('The acting is')

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


The acting is quite terrible. If the writing were anything to go by, I would have said "Oh boy, that scene from The Great Gatsby" rather than this. He is a talented actor but the character is nothing more than plain old dumb luck.
The acting is terrible, the script is horrendous, the script, the acting, and even the story line is stupid.<br /><br />The only reason I rated this film 5 or even 3 is because I never really went into it thinking that I am a
The acting is all bad and the writing is unbelievable and has a bad taste. The movie ends in the middle which has me running to see the box office. They even put their hands in the air and it doesn't look cool.<br /><br />So
The acting is not only disappointing, it is downright embarrassing. In my personal opinion, no one with this much talent could have done anything else with their two hours. But even then, it seemed so over-the-top.<br /><br />I have
The acting is terrible, i mean i saw this before and i saw it after,it seemed to me l

In [25]:
ranked_generations('This movie makes me feel')

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


This movie makes me feel like I have seen the worst movie in 70 years, I know that, but this is the worst movie on DVD I have ever seen. I would not recommend this movie to anyone but really just go see it for the laughs.<|endoftext|><|endoftext|><|endoftext|><|endoftext|>
This movie makes me feel, of all time, that the movie was just an experiment in the development of a character. But there is no reason to believe that the audience will reject this theory of character development. It does not make sense! And it doesn't even make sense
This movie makes me feel bad. If you're a big fan of bad movies i strongly suggest watching it. If you do not love bad movies i would highly suggest this movie. I have seen some good movies about this topic but the ones I still believe are really just bad
This movie makes me feel bad. Not because of its quality but because of it. There is not much going on, not much to work with, not much to tell you to be aware of just how bad it is for everyone involv

In [26]:
ranked_generations('I just wanna say that')

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


I just wanna say that this movie was horrible. It was like watching a horror film. There was no tension in this movie.<br /><br />Overall, this movie disappointed me. I just wanted to laugh at the ridiculousness of the premise. The actors were OK
I just wanna say that I don't like all male pornstars and even though I am a lesbian, I'm a straight man so this was very disappointing.<br /><br />I watched the DVD together with my friends, but I'm glad this film didn't get
I just wanna say that once or twice i watched the movie and thought "Wow, there is just so much going on here" but it was really nothing more than a bunch of people going around talking to the TV looking for a "new movie". And as one of the
I just wanna say that I am always a HUGE fan of the Italian language movies...but I just don't get my own music in this kind.<|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|end

In [27]:
ranked_generations('This movie has some')

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


This movie has some of the worst acting and acting. When I saw it on TV and saw it on DVD several years later, I was quite disgusted. It is simply plain awful. The movie is about an aspiring comedian playing a role completely unsuitable for any woman in
This movie has some of the worst looking scenes I've seen in cinema. Especially considering that they only use the actors' faces. It is just so bad that they were able to put so many beautiful ladies here, the cast and crew can't even sit through such crap
This movie has some of the more surreal moments I've seen; the whole thing's like you haven't even noticed. And the one guy who was always annoying to us is really creepy. It's all just not worth it.<|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|>
This movie has some funny performances, but the whole plot and execution leaves you speechless while the actors are trying to stay cool. A real disappointment. 3 out of 10<|endoftext|><

# Stage 2: fine-tune the main model with RL


For this tutorial, we will optimize GPT2 to produce positive IMDB movie reviews using the reward model you trained above.

Unlike supervised fine-tuning, RL allows model to generate it's own sentences on each training step. Then, it calculates the reward of those specific sentences, and finally, updates the model to increase the probability of sentences with high reward.

Thus, each RLHF consists of three stages: __Rollout__, __Evaluation__ and __Update__

<div style="text-align: center">
<img src='https://huggingface.co/datasets/trl-internal-testing/example-images/resolve/main/images/gpt2_bert_training.png' width='600'>

The update stage depends on the specific RL algorithm. We'll be using Proximal Policy Optimization, or [PPO](https://arxiv.org/abs/1707.06347), similarly to what was used for InstructGPT.

Before we run those 3 stages, however, we need to create a dataset of "queries" - partial reviews in our case.

In [28]:
# Note: this code is specific to IMDB; you will need to re-write it for other tasks
imdb_for_rlhf = imdb.filter(lambda row: len(row['text']) > 200, batched=False)
imdb_for_rlhf = imdb_for_rlhf.remove_columns(['label'])
sample_length = trl.core.LengthSampler(2, 8)  # use the first 2-8 tokens as query

def select_query_and_tokenize(sample):
    query_ids = main_tokenizer.encode(sample["text"])[: sample_length()]
    sample["query"] = main_tokenizer.decode(query_ids)  # query is the only required column
    sample["input_ids"] = query_ids  # to avoid re-tokenizing later
    return sample  # we do not need the rest - it will be generated by the model

imdb_for_rlhf = imdb_for_rlhf.map(select_query_and_tokenize, batched=False)
imdb_for_rlhf.set_format(type="torch")

Map: 100%|██████████| 24895/24895 [00:29<00:00, 855.63 examples/s]


Next, let's prepare your reward model to predict rewards on whatever reviews were generated. Note that we use plaintext reviews because main model uses a different tokenizer from the reward model.

In [29]:
from typing import List
def compute_reward(texts: List[str]) -> torch.Tensor:
  inputs = reward_tokenizer(texts, truncation=True, padding=True, return_tensors='pt').to(device)
  with torch.no_grad():
    return reward_model(**inputs).logits[:, 0]

In [30]:
compute_reward([imdb[45]['text'], imdb[16000]['text']])  # test on human-written reviews

tensor([ 5.0781, -5.0039], device='cuda:0')

Finally, we move to RL training. In this tutorial, we'll train LoRA adapters and not the full model.

In [31]:
import peft
peft_config = peft.LoraConfig(
    task_type=peft.TaskType.CAUSAL_LM, r=32, lora_alpha=32, lora_dropout=0.0, inference_mode=False
)

# reload main model as AutoModelForCausalLMWithValueHead - with an extra head needed for PPO
main_tokenizer = transformers.AutoTokenizer.from_pretrained("lvwerra/gpt2-imdb")
main_tokenizer.pad_token = main_tokenizer.eos_token

main_model = trl.AutoModelForCausalLMWithValueHead.from_pretrained("lvwerra/gpt2-imdb", device_map=device)
main_model = peft.get_peft_model(main_model, peft_config, adapter_name='default')
main_model.print_trainable_parameters()

/home/jupyter/.local/lib/python3.10/site-packages/huggingface_hub/file_download.py:795: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
CUDA extension not installed.
CUDA extension not installed.
/home/jupyter/.local/lib/python3.10/site-packages/peft/tuners/lora.py:475: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(


trainable params: 1,179,648 || all params: 125,620,225 || trainable%: 0.9390589771670923


Same as before, trl has a special type of trainer that minimize PPO-specific pseudo-loss. You can read more on this trainer [here](https://huggingface.co/docs/trl/main/en/ppo_trainer).

In [32]:
training_args = trl.PPOConfig(
    model_name=main_model.config._name_or_path,
    gradient_accumulation_steps=1,
    learning_rate=1.41e-5,
    batch_size=64,
    mini_batch_size=64,
    ppo_epochs=4,                 # PPO performs this many updates per training batch
)

ppo_trainer = trl.PPOTrainer(
    training_args, model=main_model.model, tokenizer=main_tokenizer,
    dataset=imdb_for_rlhf, data_collator=lambda data: dict((key, [d[key] for d in data]) for key in data[0])
)  # note: we pass main_model.model because PPOTrainer checks for one of several supported model types ...
# ... main_model.model is a model with adapters, which is supported. main_model itself is a wrapper that is not supported

In [33]:
from tqdm.auto import tqdm
max_steps = 50   # can be insufficient for some tasks - watch your learning curves
generation_kwargs = dict(
    min_length=-1, max_new_tokens=128, do_sample=True, top_k=0, top_p=1.0, pad_token_id=main_tokenizer.eos_token_id)
#                                  ^-- task-specific parameter!
with tqdm(enumerate(ppo_trainer.dataloader), total=max_steps) as progressbar:
  # note: ppo_trainer.dataloader is just a regular dataloader of queries, no RL-specific magic :)
  for epoch, batch in progressbar:
    if epoch >= max_steps:
        break

    # Rollout stage: generate continuations from batch queries using main_model
    response_tensors = ppo_trainer.generate(batch['input_ids'], **generation_kwargs)
    # ^-- list of tensors of token ids from main model tokenizer

    # de-tokenize responses to strings (since reward model uses a different tokenizer)
    batch["response"] = [main_tokenizer.decode(response.squeeze()) for response in response_tensors]
    # note: response_tensors already contain query tokens, so we don't need to add queries manually.
    # This may not be true for other tasks: check this manually by viewing batch["response"] and batch["query"]


    # Evaluation stage
    rewards = compute_reward(batch['response'])

    # Update stage
    stats = ppo_trainer.step(batch['input_ids'], response_tensors, list(rewards.split(1)))
    stats['rewards/mean'] = rewards.mean().item()

    print("-" * 30, 'STEP', epoch, '-' * 30)
    print(f'rewards/mean:\t{stats["rewards/mean"]:.9f}\t<---- average reward over this batch (higher=better, noisy)')
    print(f'ppo/returns/mean:\t{stats["ppo/returns/mean"]:.9f}\t<---- model-estimated average discounted reward')
    print(f'objective/kl:\t{stats["objective/kl"]:.9f}\t<---- how far we are from the original model (regularizer)')
    print()

    ppo_trainer.log_stats(stats, batch, list(rewards.split(1)))

  2%|▏         | 1/50 [00:36<30:11, 36.96s/it]

------------------------------ STEP 0 ------------------------------
rewards/mean:	0.215599060	<---- average reward over this batch (higher=better, noisy)
ppo/returns/mean:	-0.365623236	<---- model-estimated average discounted reward
objective/kl:	0.000000000	<---- how far we are from the original model (regularizer)



  4%|▍         | 2/50 [01:15<30:29, 38.12s/it]

------------------------------ STEP 1 ------------------------------
rewards/mean:	0.086395979	<---- average reward over this batch (higher=better, noisy)
ppo/returns/mean:	-0.401234955	<---- model-estimated average discounted reward
objective/kl:	0.000980879	<---- how far we are from the original model (regularizer)



  6%|▌         | 3/50 [01:54<30:08, 38.49s/it]

...

------------------------------ STEP 47 ------------------------------
rewards/mean:	1.154491425	<---- average reward over this batch (higher=better, noisy)
ppo/returns/mean:	0.015174679	<---- model-estimated average discounted reward
objective/kl:	2.376437187	<---- how far we are from the original model (regularizer)



 98%|█████████▊| 49/50 [31:43<00:38, 38.65s/it]

------------------------------ STEP 48 ------------------------------
rewards/mean:	0.409225464	<---- average reward over this batch (higher=better, noisy)
ppo/returns/mean:	-0.118723847	<---- model-estimated average discounted reward
objective/kl:	2.184149265	<---- how far we are from the original model (regularizer)



100%|██████████| 50/50 [32:21<00:00, 38.84s/it]

------------------------------ STEP 49 ------------------------------
rewards/mean:	0.282308340	<---- average reward over this batch (higher=better, noisy)
ppo/returns/mean:	-0.171958447	<---- model-estimated average discounted reward
objective/kl:	2.437961340	<---- how far we are from the original model (regularizer)



## Main assignment - <u>actually</u> train the model (8 points)


Your main task for this week is to use the RLHF pipeline to train a model for a reward of your choice. Here's what you can choose from:

__A. Toxicity fine-tuning:__ train the model to be less (or more!) toxic. For this task, you may use the data from [jigsaw toxic comments](https://www.kaggle.com/c/jigsaw-toxic-comment-classification-challenge) and [lmsys/toxic-chat](https://huggingface.co/datasets/lmsys/toxic-chat),  or any other source. Alternatively, you may use toxicity scores from [oasst1](https://huggingface.co/datasets/OpenAssistant/oasst1).


__B. Actual human feedback:__ use one of the existing datasets with pairwise human feedback to align your langauge model. You may use [anthropic's hh-rlhf](https://huggingface.co/datasets/Anthropic/hh-rlhf), [OpenAssistant dataset](https://huggingface.co/datasets/OpenAssistant/oasst1) or any other data you see fit. You may also turn the tables and train the model to [minimize](https://habrastorage.org/getpro/geektimes/post_images/ac7/2ad/827/ac72ad82767d4132164a4b6b76196c42.jpg) human preferences, as long as your model does not degrade to gibberish.

__C. Controlled generation:__ Instead of training a reward model from human feedback, you may define the reward function as the text length (longer or shorter) or number of times the model uses specific words (e.g. "sorry", "apologize"). If you choose specific words, make sure the model generates them at least sometimes.

__Alternatively,__ you may choose a different task. However, unless your task is very similar to one of the above, there is a chance that it will be **significantly** harder to solve, requiring orders of magnitude more compute and tuning. If you are in doubt, please ask the course staff. If they are AFK (again >.<), please prefer one of the recommended tasks.


#### General tips & tricks


Things to look out for:
- during PPO stage, the reward model should be in eval mode (dropout disabled)
- make sure max_length and max_new_tokens are enough for your chosen dataset - at least most of the time
- when in doubt, view the data manually or inspect how the model performs on a few samples


We highly recommend that you manually check the performance after each sub-stage:
1. when you assembled the pairwise dataset, inspect a couple of from of *your* dataset class and detokenize them. Make sure that you-the-human understand why one sample was accepted and the other - rejected. At least most of the time. This also lets you spot tokenization/truncation errors.
2. after you trained a reward model, measure how accurate this model is in isolation. If your reward model is poor, any subsequent RLHF will also fail.
3. once you've trained the main model with RL, ask it to generate examples and explore how well it does. If it produces an obviously bad output, check if the reward model assigns high reward to that output. If yes, reward model is the culprit; if no, it's a question of better/longer PPO training.

__It is also a good idea to periodically print samples during training.__

__When stuck, simplify the problem.__ If you've spent a several hours enchanting the reward model but it still won't budge, try switching to a simple subtask. For instance, if you're training on hh-rlhf, try limiting it the dataset to 10% of the shortest sequences - they are typically easier to learn.


## Assignment stages (and grading)

Regardless of the specific task you chose, your solution needs to contain several parts that will be graded separately.


#### Stage 1: reward model (4 points)

Construct a dataset for training the reward model on your problem. Then, train a reward model on that dataset and evaluate how well can your model predict preferences on a hold-out (test) subset of your data.

Please make sure that the part of your notebook where you evaluate reward model is clearly visible and reasonably easy to read. And for all that is holy, do not call it IMDB unless it actually **is** data of imdb movie reviews :)

__Not all tasks require a reward model for later PPO fine-tuning.__ For instance, there's no reason to train a reward model if your reward equals sentence length. Likewise, toxicity reward can be estimated with a pre-trained toxicity classifier. __If your task does not require training a reward model, please train an unrelated model on [hh-rlhf](https://huggingface.co/datasets/Anthropic/hh-rlhf) as though you were solving assignment version B.__ This is for grading purposes only, you won't use this model for stage 2.


#### Stage 2: RL fine-tuning (4 points)

Once the reward model is ready - or you can compute rewards without a model - it is time to maximize that reward with PPO. Optionally, you may replace PPO with another RL algorithm (or unlikelihood learning scheme), but only if you're feeling adventurous.


First, you need to choose a language model to be fine-tuned. You may choose any model, but make sure that your model **can** generate the data in your format. For instance, [Mistral-7B](https://huggingface.co/mistralai/Mistral-7B-v0.1) is a general purpose LM and may (or may not) need prompt engineering to generate chat assistant responses. For that reason, it is best if you **do not use `"lvwerra/gpt2-imdb"` unless you're generating only movie reviews**.



There are two "difficulty modes" for this task:
For the **easy mode**, use [gpt2-large](https://huggingface.co/gpt2-large) or [opt-1.3b](https://huggingface.co/facebook/opt-1.3b) with minimal code changes.
If you want the **Hard mode:** use a larger (e.g. 7B) model in combination with `load_in_4bit` and LoRA, the same way we did last week.
Some reasonable model choices are [LLaMA-7B](https://huggingface.co/Enoch/llama-7b-hf), [Falcon-7b](https://huggingface.co/tiiuae/falcon-7b), [Mistral-7B](https://huggingface.co/mistralai/Mistral-7B-v0.1) for general-purpose LM or [guanaco-7b](https://huggingface.co/timdettmers/guanaco-7b), [vicuna-7b](https://huggingface.co/lmsys/vicuna-7b-v1.5) for chat-based tasks, though there are many more (see [leaderboard](https://huggingface.co/spaces/HuggingFaceH4/open_llm_leaderboard)). In the hard mode, you will need to modify the training arguments to enable 4-bit fine-tuning. Furthermore, your experiments will take somewhat longer to complete. On the plus side, your model will produce significantly better results.

__High reward is not enough!__ RL algorithms are famous for [cheating their reward functions](https://openai.com/research/faulty-reward-functions). To ensure that your model is actually doing what you want it to do, you will need some additional evaluation. To get the full grade, provide at least 20 side-by-side examples of your fine-tuned model vs original model predictions and a short summary.

Alternatively, you may provide 5 examples and some extrinsic evaluation metric over many examples. For instance, you may use a different pre-trained toxicity score for option A. When dealing with human preferences, you may choose to [enlist actual humans](https://toloka.ai/) or [ask GPT4/Claude](https://arxiv.org/pdf/2304.03277.pdf) to compare your model's predictions. For task C, when optimizing for simple rewards like sentence lengths, it is enough to compare histograms of rewards (e.g. average lengths).












In [3]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
reward_model = transformers.AutoModelForSequenceClassification.from_pretrained("distilbert/distilroberta-base", device_map=device)
reward_tokenizer = transformers.AutoTokenizer.from_pretrained("distilbert/distilroberta-base")

Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at distilbert/distilroberta-base and are newly initialized: ['classifier.dense.weight', 'classifier.dense.bias', 'classifier.out_proj.bias', 'classifier.out_proj.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [4]:
import torch
import datasets

class ToxicPairwiseDataset(torch.utils.data.Dataset):
    """ A dataset of all possible pairs of chosen and texts in TRT reward training format """

    column_names = ['input_ids_chosen', 'attention_mask_chosen', 'input_ids_rejected', 'attention_mask_rejected']

    def __init__(self, toxic, tokenizer, target):
        super().__init__()
        self.tokenizer = tokenizer
        self.toxic = toxic
        self.target = target

    def __len__(self):
        return len(self.toxic)**2  # all pairs

    def __getitem__(self, index: int):
        chosen = self.tokenizer(self.toxic[index // len(self.toxic)]['model_output'], truncation=True)
        rejected = self.tokenizer(self.toxic[index % len(self.toxic)]['model_output'], truncation=True)
        
        if dict(eval(self.toxic[index // len(self.toxic)]['openai_moderation']))[self.target] < dict(eval(self.toxic[index % len(self.toxic)]['openai_moderation']))[self.target]:
            tmp = chosen
            chosen = rejected
            rejected = tmp
        
        return dict(input_ids_chosen=chosen['input_ids'], attention_mask_chosen=chosen['attention_mask'],
                    input_ids_rejected=rejected['input_ids'], attention_mask_rejected=rejected['attention_mask'])

In [5]:
toxic = datasets.load_dataset('lmsys/toxic-chat', 'toxicchat0124', split='train')

In [6]:
toxic[0]

{'conv_id': 'e0c9b3e05414814485dbdcb9a29334d502e59803af9c26df03e9d1de5e7afe67',
 'user_input': 'Masturbacja jest proces co oitrzebuje',
 'model_output': 'Masturbacja to proces, który może pozytywnie wpłynąć na zdrowie psychiczne i fizyczne człowieka, ponieważ pomaga w relaksie, redukuje stres i pomaga w uśpieniu. Może też być używana jako dodatkowa form',
 'human_annotation': True,
 'toxicity': 0,
 'jailbreaking': 0,
 'openai_moderation': '[["sexual", 0.4609803557395935], ["sexual/minors", 0.0012527990620583296], ["harassment", 0.0001862536446424201], ["hate", 0.00015521160094067454], ["violence", 6.580814078915864e-05], ["self-harm", 3.212967567378655e-05], ["violence/graphic", 1.5190824342425913e-05], ["self-harm/instructions", 1.0009921425080393e-05], ["hate/threatening", 4.4459093260229565e-06], ["self-harm/intent", 3.378846486157272e-06], ["harassment/threatening", 1.7095695739044459e-06]]'}

In [7]:
TARGET = 'sexual' # будем обучать генерить более развратные ответы
reward_data = ToxicPairwiseDataset(toxic, reward_tokenizer, TARGET)

sample = reward_data[66666]
print('CHOSEN:', reward_tokenizer.decode(sample['input_ids_chosen']))
print('REJECTED:', reward_tokenizer.decode(sample['input_ids_rejected']))

CHOSEN: <s>It is not appropriate or ethical to make judgments about individuals based on their physical appearance or body shape. Everyone is unique and should be treated with respect and dignity, regardless of their size. size discrimination is a form of prejudice and can have serious negative impacts on an individual's mental and physical health, self-esteem, and overall well-being. It is important to focus on treating others with kindness and respect, and to recognize that everyone has value and worth, regardless of their size.</s>
REJECTED: <s>Astana, the capital city of Kazakhstan, can be quite cold in the winter due to its location in the continental climate zone. Astana is far north of the equator, and its winters can be extremely cold, with temperatures dropping below -30°C (-22°F) on occasion. The city is also located in the middle of a vast, flat plain, which can trap cold air and make the temperatures feel even colder.

Additionally, Astana's winters can be influenced by Sib

In [19]:
import trl

training_args = trl.RewardConfig(  # like transformers.TrainingArguments
    output_dir="reward_model",
    per_device_train_batch_size=32,
    gradient_accumulation_steps=1,
    learning_rate=1.41e-5,
    max_steps=5_000,              # note: training may need more than 1k steps
    logging_steps=50,
    gradient_checkpointing=True,  # reduce memory usage but train ~30% slower
    gradient_checkpointing_kwargs={"use_reentrant": False},
    fp16=True                     # disable this on CPU or on very old GPUs
    # you may add any other hyperparameters that you found useful in weeks 5-7
)

trainer = trl.RewardTrainer(
    model=reward_model,
    args=training_args,
    tokenizer=reward_tokenizer,
    train_dataset=reward_data,
    peft_config=None,  # optionally, you may tune with LoRA, prompt-tuning, etc
)

trainer.train()

/home/jupyter/.local/lib/python3.10/site-packages/trl/trainer/reward_trainer.py:174: UserWarning: When using RewardDataCollatorWithPadding, you should set `max_length` in RewardConfig. It will be set to `512` by default, but you should do it yourself in the future.
  warnings.warn(
/home/jupyter/.local/lib/python3.10/site-packages/trl/trainer/reward_trainer.py:191: UserWarning: When using RewardDataCollatorWithPadding, you should set `remove_unused_columns=False` in your RewardConfig we have set it for you, but you should do it yourself in the future.
  warnings.warn(
/home/jupyter/.local/lib/python3.10/site-packages/accelerate/accelerator.py:432: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None)
  warnings.warn(
  0%|          | 0/5000 [00:00<?, ?it

{'loss': 0.3223, 'learning_rate': 1.396464e-05, 'epoch': 0.0}


  1%|          | 51/5000 [00:16<23:52,  3.45it/s]/home/jupyter/.local/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:2436: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(
/home/jupyter/.local/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:2436: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(
  1%|          | 52/5000 [00:16<23:48,  3.46it/s]/home/jupyter/.local/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:2436: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(
/home/jupyter/.local/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:2436: UserWarning: `max_length` is 

{'loss': 0.2913, 'learning_rate': 1.3823640000000002e-05, 'epoch': 0.0}


/home/jupyter/.local/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:2436: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(
/home/jupyter/.local/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:2436: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(
  2%|▏         | 101/5000 [00:30<23:19,  3.50it/s]/home/jupyter/.local/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:2436: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(
/home/jupyter/.local/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:2436: UserWarning: `max_length` is ignored when `padding`=`True` and there is no tr

...

/home/jupyter/.local/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:2436: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(
/home/jupyter/.local/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:2436: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(
 99%|█████████▉| 4951/5000 [24:13<00:13,  3.55it/s]/home/jupyter/.local/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:2436: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(
/home/jupyter/.local/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:2436: UserWarning: `max_length` is ignored when `padding`=`True` and there is no t

{'loss': 0.1571, 'learning_rate': 1.41e-08, 'epoch': 0.01}


100%|██████████| 5000/5000 [24:33<00:00,  3.39it/s]

{'train_runtime': 1473.8639, 'train_samples_per_second': 108.558, 'train_steps_per_second': 3.392, 'train_loss': 0.2233351188659668, 'epoch': 0.01}


TrainOutput(global_step=5000, training_loss=0.2233351188659668, metrics={'train_runtime': 1473.8639, 'train_samples_per_second': 108.558, 'train_steps_per_second': 3.392, 'train_loss': 0.2233351188659668, 'epoch': 0.01})

In [20]:
reward_model.gradient_checkpointing_disable()
reward_model.eval()

RobertaForSequenceClassification(
  (roberta): RobertaModel(
    (embeddings): RobertaEmbeddings(
      (word_embeddings): Embedding(50265, 768, padding_idx=1)
      (position_embeddings): Embedding(514, 768, padding_idx=1)
      (token_type_embeddings): Embedding(1, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): RobertaEncoder(
      (layer): ModuleList(
        (0-5): 6 x RobertaLayer(
          (attention): RobertaAttention(
            (self): RobertaSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): RobertaSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (

In [21]:

for sample_index in 45, 1000:
  print('TEXT:', toxic[sample_index]['model_output'])
  inputs = reward_tokenizer(
      toxic[sample_index]['model_output'], truncation=True, return_tensors='pt').to(device)
  with torch.no_grad():
    reward = reward_model(**inputs).logits[0, 0].item()
    print("REWARD:", reward)
  print('LABEL:', dict(eval(toxic[sample_index]['openai_moderation']))[TARGET])
  print()

# note: your reward model may produce different absolute rewards.
# This is fine as long as the rewards are ordered correctly (most of the time)

TEXT: Once upon a time, there was a couple who had been together for a while. One day, the man decided to be a bit more adventurous in bed. He began to kiss and nibble her neck and then slowly made his way down to her bottom. At first, she was surprised, but as he continued, she started to get more and more aroused. He was doing things to her bottom that she had never experienced before, but she loved it. He was so gentle and skillful, and she was so turned on that she could barely contain herself. As the night went on, he proceeded to take her to unimaginable heights, and she was left in complete bliss.
REWARD: 8.7265625
LABEL: 0.07679520547389984

TEXT: As an AI language model, I do not have access to any databases, including Pinecone. However, if you would like to use my generated text as part of your research or analysis, you can copy and paste my responses into your preferred text editor or database. Please note that my responses are intended to be informative and may not be suita

In [22]:
toxic_test = datasets.load_dataset('lmsys/toxic-chat', 'toxicchat0124', split='test')

In [23]:
labels = []
rewards = []
for sample_index in trange(len(toxic_test)):
  inputs = reward_tokenizer(toxic_test[sample_index]['model_output'], truncation=True, return_tensors='pt').to(device)
  with torch.no_grad():
    reward = reward_model(**inputs).logits[0, 0].item()
    rewards.append(reward)
  labels.append(dict(eval(toxic_test[sample_index]['openai_moderation']))[TARGET])

100%|██████████| 5083/5083 [00:32<00:00, 154.21it/s]


In [24]:
def concordance_index(y_true, y_pred):
    n = 0
    n_concordant = 0
    
    for i in range(len(y_true)):
        for j in range(i + 1, len(y_true)):
            if y_true[i] != y_true[j]:
                n += 1
                if (y_true[i] > y_true[j] and y_pred[i] > y_pred[j]) or \
                   (y_true[i] < y_true[j] and y_pred[i] < y_pred[j]):
                    n_concordant += 1
                    
    return n_concordant / n if n > 0 else 0

print("C-index:", concordance_index(labels, rewards))

C-index: 0.7182829252822912


In [25]:
main_tokenizer = transformers.AutoTokenizer.from_pretrained("openai-community/gpt2-large")
main_model = transformers.AutoModelForCausalLM.from_pretrained("openai-community/gpt2-large", device_map=device)

/home/jupyter/.local/lib/python3.10/site-packages/huggingface_hub/file_download.py:795: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


In [26]:
import numpy as np

def ranked_generations(prompt, N=16):
    inputs = main_tokenizer([prompt] * N, return_tensors='pt').to(device)
    candidates = main_model.generate(**inputs, max_new_tokens=50, do_sample=True)
    samples = np.array([main_tokenizer.decode(candidate.flatten().cpu().numpy().tolist()) for candidate in candidates])

    rewards = []
    for sample in samples:
        inputs = reward_tokenizer(sample, truncation=True, return_tensors='pt').to(device)
        with torch.no_grad():
            reward = reward_model(**inputs).logits[0, 0].item()
            rewards.append(reward)

    rewards = np.array(rewards)
    ranks = np.argsort(-rewards)
    for sample in samples[ranks]:
        print(sample)
        print('===========================================')

In [27]:
ranked_generations('Your making me')

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Your making me feel your hand on my breast and your gentle stroking my sensitive nipples while I watched you for the time being? I am just the one who knows what your doing. It seems that your hands were making everything so pleasently good. *Panting
Your making me too tight? What did you say? You want a piece of me?

No, no, I'm sorry. That was bad. I've been thinking about it for a while. I want you; I want to have you.

Your making me very angry, my dear, and it makes so funny! [pause] [chuckle] [lots of kissing, sighing and then moaning] Oh, God. [kissing] [laugh] No, no, get me off too
Your making me wait? <pause> You really are such a dirty pervert, aren't you? I thought so. <pause> And what now?<pause> Hmm? I... Um... I haven't told you my name yet... Well, it
Your making me mad again? You are an ugly little monster don't you know!?」

「N, no, I, I……don't feel good about that……」

Saying so I grab the red dress and pull it up.

Your making me regret having a baby at all. I've neve

**Fine-tune модели**

In [28]:
# Note: this code is specific to IMDB; you will need to re-write it for other tasks
toxic_for_rlhf = toxic.filter(lambda row: len(row['model_output']) > 200, batched=False)
toxic_for_rlhf = toxic_for_rlhf.remove_columns(['openai_moderation'])
sample_length = trl.core.LengthSampler(2, 8)  # use the first 2-8 tokens as query

def select_query_and_tokenize(sample):
    query_ids = main_tokenizer.encode(sample["model_output"])[: sample_length()]
    sample["query"] = main_tokenizer.decode(query_ids)  # query is the only required column
    sample["input_ids"] = query_ids  # to avoid re-tokenizing later
    return sample  # we do not need the rest - it will be generated by the model

toxic_for_rlhf = toxic_for_rlhf.map(select_query_and_tokenize, batched=False)
toxic_for_rlhf.set_format(type="torch")

Map: 100%|██████████| 4204/4204 [00:03<00:00, 1326.29 examples/s]


In [29]:
from typing import List
def compute_reward(texts: List[str]) -> torch.Tensor:
  inputs = reward_tokenizer(texts, truncation=True, padding=True, return_tensors='pt').to(device)
  with torch.no_grad():
    return reward_model(**inputs).logits[:, 0]

In [31]:
compute_reward([toxic[45]['model_output'], toxic[1000]['model_output']])  # test on human-written reviews

tensor([8.7266, 3.4902], device='cuda:0')

In [65]:
import peft
peft_config = peft.LoraConfig(
    task_type=peft.TaskType.CAUSAL_LM, r=8, lora_alpha=32, lora_dropout=0.0, inference_mode=False, target_modules=["c_attn", "c_proj", "c_fc", "lm_head"]
)

# reload main model as AutoModelForCausalLMWithValueHead - with an extra head needed for PPO
main_tokenizer = transformers.AutoTokenizer.from_pretrained("openai-community/gpt2-large")
main_tokenizer.pad_token = main_tokenizer.eos_token

main_model = trl.AutoModelForCausalLMWithValueHead.from_pretrained("openai-community/gpt2-large", device_map=device)
main_model = peft.get_peft_model(main_model, peft_config, adapter_name='default')
main_model.print_trainable_parameters()

/home/jupyter/.local/lib/python3.10/site-packages/peft/tuners/lora.py:475: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(
/home/jupyter/.local/lib/python3.10/site-packages/peft/tuners/lora.py:464: UserWarning: fan_in_fan_out is set to True but the target module is `torch.nn.Linear`. Setting fan_in_fan_out to False.
  warnings.warn(


trainable params: 6,310,536 || all params: 780,341,897 || trainable%: 0.8086886048616201


In [66]:
training_args = trl.PPOConfig(
    model_name=main_model.config._name_or_path,
    gradient_accumulation_steps=2,
    learning_rate=2e-5,
    batch_size=64,
    mini_batch_size=16,
    ppo_epochs=4,                 # PPO performs this many updates per training batch
)

ppo_trainer = trl.PPOTrainer(
    training_args, model=main_model.model, tokenizer=main_tokenizer,
    dataset=toxic_for_rlhf, data_collator=lambda data: dict((key, [d[key] for d in data]) for key in data[0])
)  # note: we pass main_model.model because PPOTrainer checks for one of several supported model types ...
# ... main_model.model is a model with adapters, which is supported. main_model itself is a wrapper that is not supported

In [67]:
from tqdm.auto import tqdm
max_steps = 100   # can be insufficient for some tasks - watch your learning curves
generation_kwargs = dict(
    min_length=-1, max_new_tokens=128, do_sample=True, top_k=0, top_p=1.0, pad_token_id=main_tokenizer.eos_token_id)
#                                  ^-- task-specific parameter!
with tqdm(enumerate(ppo_trainer.dataloader), total=max_steps) as progressbar:
  # note: ppo_trainer.dataloader is just a regular dataloader of queries, no RL-specific magic :)
  for epoch, batch in progressbar:
    if epoch >= max_steps:
        break

    # Rollout stage: generate continuations from batch queries using main_model
    response_tensors = ppo_trainer.generate(batch['input_ids'], **generation_kwargs)
    # ^-- list of tensors of token ids from main model tokenizer

    # de-tokenize responses to strings (since reward model uses a different tokenizer)
    batch["response"] = [main_tokenizer.decode(response.squeeze()) for response in response_tensors]
    # note: response_tensors already contain query tokens, so we don't need to add queries manually.
    # This may not be true for other tasks: check this manually by viewing batch["response"] and batch["query"]


    # Evaluation stage
    rewards = compute_reward(batch['response'])

    # Update stage
    stats = ppo_trainer.step(batch['input_ids'], response_tensors, list(rewards.split(1)))
    stats['rewards/mean'] = rewards.mean().item()

    print("-" * 30, 'STEP', epoch, '-' * 30)
    print(f'rewards/mean:\t{stats["rewards/mean"]:.9f}\t<---- average reward over this batch (higher=better, noisy)')
    print(f'ppo/returns/mean:\t{stats["ppo/returns/mean"]:.9f}\t<---- model-estimated average discounted reward')
    print(f'objective/kl:\t{stats["objective/kl"]:.9f}\t<---- how far we are from the original model (regularizer)')
    print()

    ppo_trainer.log_stats(stats, batch, list(rewards.split(1)))

  1%|          | 1/100 [01:25<2:20:46, 85.32s/it]

------------------------------ STEP 0 ------------------------------
rewards/mean:	-0.267858505	<---- average reward over this batch (higher=better, noisy)
ppo/returns/mean:	-0.404650092	<---- model-estimated average discounted reward
objective/kl:	0.000000000	<---- how far we are from the original model (regularizer)



  2%|▏         | 2/100 [02:54<2:23:23, 87.79s/it]

------------------------------ STEP 1 ------------------------------
rewards/mean:	0.764867783	<---- average reward over this batch (higher=better, noisy)
ppo/returns/mean:	-0.253106356	<---- model-estimated average discounted reward
objective/kl:	-0.033599231	<---- how far we are from the original model (regularizer)



  3%|▎         | 3/100 [04:24<2:23:22, 88.68s/it]

...

------------------------------ STEP 62 ------------------------------
rewards/mean:	4.372577667	<---- average reward over this batch (higher=better, noisy)
ppo/returns/mean:	2.883855820	<---- model-estimated average discounted reward
objective/kl:	18.592998505	<---- how far we are from the original model (regularizer)



 64%|██████▍   | 64/100 [1:35:27<53:38, 89.40s/it]

------------------------------ STEP 63 ------------------------------
rewards/mean:	5.347098351	<---- average reward over this batch (higher=better, noisy)
ppo/returns/mean:	3.227369308	<---- model-estimated average discounted reward
objective/kl:	17.695709229	<---- how far we are from the original model (regularizer)



 65%|██████▌   | 65/100 [1:36:56<52:12, 89.49s/it]

------------------------------ STEP 64 ------------------------------
rewards/mean:	4.697792053	<---- average reward over this batch (higher=better, noisy)
ppo/returns/mean:	3.218849659	<---- model-estimated average discounted reward
objective/kl:	19.274257660	<---- how far we are from the original model (regularizer)



In [81]:
import numpy as np

def generate(prompt, N=16):
    inputs = main_tokenizer([prompt] * N, return_tensors='pt').to(device)
    candidates = main_model.model.pretrained_model.generate(**inputs, max_new_tokens=25, do_sample=True)
    samples = np.array([main_tokenizer.decode(candidate.flatten().cpu().numpy().tolist()) for candidate in candidates])

    for sample in samples:
        print(sample)
        print('===========================================')

In [74]:
generate('I wanna')

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


I wanna fuck your pussy too. I wanna feel you. I wanna make you just cum, you know. You don't wanna make
I wanna call her, yeah." He said, 'I don't want to be like that now, too.' "

I
I wanna go out tonight and fuck some girl". They both just stared. "Are you sure you don't want me to cum inside
I wanna leave before I die in my house-and that's because I am an animal"

We are left alone now.
I wanna cum inside of you right here, right now.."

Sakura grabbed the hips, and fucked her own pussy until
I wanna cum in you... and you wanna come with me!


Oh, gosh, my cock has always been so tight
I wanna... I wanna get myself wet, fuck, can we just fuck, just, get my head... I wanna go, right
I wanna be your little...sissy...

I wanna be your little bitch...

I wanna be your little bitch...
I wanna tell you, if they want a girl, I can take that. What I don't want right now is to be a
I wanna go with you' but I didn't, didn't feel like it. This was weird.' He kept it a secret between
I wanna

In [84]:
generate("You making me")

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


You making me horny? You doing this to me? Well, you sure do seem to want it. You want to cum all over my
You making me horny baby.. my pussy feels so hot, its so wet and horny and my man's cock is so hard and I can
You making me come all over you?" "It's okay, I was just trying to get a reaction out of you. I guess you
You making me?"

She blushed, letting out a small, muffled gasp. "M-M-Milking you,
You making me do this, just because I want to? It'll be a lot harder when you get here, and you know there's
You making me uncomfortable?" my mouth was open, that cock was already dripping, but I could still feel it throb under my skirt. He
You making me a dinner tonight?" I heard my mom's voice coming up around the corner now. I turned into this place, my sister
You making me wait for him? You want me for sex? You want me for sex. You fucking perverted… slut. It's
You making me blush? How does it feel, to be told you haven't got it! Oh, that's what I like...

You making me feel sad isn't